In [1]:
import json

all_edits = json.loads(open('result.json', 'r', encoding='utf8').read())

In [24]:
def search(edit_type_q=None, head_q={}, target_q={}, child_q={}, delete_q={}):
    groups = filter(lambda e: e['edit_type'] == edit_type_q, all_edits) if edit_type_q else all_edits
    
    def extract(group, node):
        return map(lambda e: e[node], group['edits']) 
        
    def match(nodes, query):
        for node in nodes:
            if not node: continue
            
            correct = sum([query[key] == node[key] for key in query])
            if correct == len(query):
                return True
        return False
    
    if head_q:
        groups = filter(lambda g: match(extract(g, 'Head'), head_q), groups)
    
    if target_q:
        groups = filter(lambda g: match(extract(g, 'Target'), target_q), groups)
    
    if child_q:
        get_childs = lambda g: [c for child in extract(g, 'Child') for c in child] # Extract and flatten
        groups = filter(lambda g: match(get_childs(g), child_q), groups)
    
    if delete_q:
        get_deletes = lambda g: [d for delete in extract(g, 'Delete') for d in delete] # Extract and flatten
        groups = filter(lambda g: match(get_deletes(g), delete_q), groups)


        
        
    def format_line(node):
        return node['token'] + "\t" + node['lemma'] + "\t" + node['tag'] + "\t" + \
            (node['dep'] if 'dep' in node and node['dep'] else '')
        
    for group in groups:
        print("==========================")
        print("type:", group['edit_type'])
        print("sent:", group['sent'])
        print()
        
        for edit in group['edits']:
            head, target, childs, deletes = edit['Head'], edit['Target'], edit['Child'], edit['Delete']
            
            ########
            if target_q and not match([target], target_q): continue
            ########
            
            if head: print("Head:\t" + format_line(head))
            if target: print("Target:\t" + format_line(target))
                
            for child in childs:
                print("Child:\t" + format_line(child))
            
            print()
            for delete in deletes:
                print("Delete:\t" + format_line(delete))
            print()

In [ ]:
'''
1. edit_type = "Delete", "Replace", "Insert", "" 四種選項

放置要過濾的 property，如果沒的話移除即可。
2. head_q,  target_q, child_q, delete_q = {
    "token": "",
    "lemma": "",
    "tag": "",
    "dep": ""
}


'''

search(edit_type_q='Delete', child_q={'token': 'to'})


type: Delete
sent: I like [-to-] listening to music , I love playing guitar and to sing .

Head:	love	love	VBP	
Target:	like	like	VBP	ccomp
Child:	I	-PRON-	PRP	nsubj
Child:	listening	listen	VBG	xcomp

Delete:	to	to	TO	

Head:	like	like	VBP	
Target:	listening	listen	VBG	xcomp
Child:	to	to	IN	prep

Delete:	to	to	TO	

type: Delete
sent: space At the same time , they began to [-have-] fish for a living .

Head:	fish	fish	VB	
Target:	to	to	TO	aux

Delete:	have	have	VBP	

Head:	began	begin	VBD	
Target:	fish	fish	VB	xcomp
Child:	to	to	TO	aux
Child:	for	for	IN	prep

Delete:	have	have	VBP	

type: Delete
sent: The weather for today : It ' 's going to [-be-] rain all afternoon and all night .

Head:	rain	rain	VB	
Target:	to	to	TO	aux

Delete:	be	be	VB	

Head:	going	go	VBG	
Target:	rain	rain	VB	xcomp
Child:	to	to	TO	aux
Child:	afternoon	afternoon	NN	npadvmod

Delete:	be	be	VB	

type: Delete
sent: I will want you to assist me to [-.-] buy , See you .

Head:	buy	buy	VB	
Target:	to	to	TO	aux

Delete:

Delete:	your	-PRON-	PRP$	
Delete:	way	way	NN	
Delete:	in	in	IN	
Delete:	my	-PRON-	PRP$	
Delete:	society	society	NN	

Head:	Let	let	VB	
Target:	.	.	.	punct

Delete:	about	about	IN	
Delete:	your	-PRON-	PRP$	
Delete:	way	way	NN	
Delete:	in	in	IN	
Delete:	my	-PRON-	PRP$	
Delete:	society	society	NN	

type: Delete
sent: I have a book to sell [-for-] you .

Head:	book	book	NN	
Target:	sell	sell	VB	relcl
Child:	to	to	TO	aux
Child:	you	-PRON-	PRP	dobj

Delete:	for	for	IN	

Head:	sell	sell	VB	
Target:	you	-PRON-	PRP	dobj

Delete:	for	for	IN	

type: Delete
sent: I would like to enquire [-you-] about the possibility of requesting a loan .

Head:	like	like	VB	
Target:	enquire	enquire	VB	xcomp
Child:	to	to	TO	aux
Child:	about	about	IN	prep

Delete:	you	-PRON-	PRP	

Head:	enquire	enquire	VB	
Target:	about	about	IN	prep
Child:	possibility	possibility	NN	pobj

Delete:	you	-PRON-	PRP	

type: Delete
sent: Nevertheless , I have to propose [-you-] another date and hope you will be able to come .

Head:	hav

type: Delete
sent: I went to the doctor and he asked me to stay [-in　bed-] at home .

Head:	asked	ask	VBD	
Target:	stay	stay	VB	xcomp
Child:	to	to	TO	aux
Child:	at	at	IN	prep

Delete:	in	in	IN	
Delete:	bed	bed	NN	

Head:	stay	stay	VB	
Target:	at	at	IN	prep
Child:	home	home	NN	pobj

Delete:	in	in	IN	
Delete:	bed	bed	NN	

type: Delete
sent: In addition , the benefits available for this position are absolutely fantastic , including full accident insurance , one month holiday every year and regular trips to Florida and other places to observe [-the-] wild crocodiles .

Head:	are	be	VBP	
Target:	observe	observe	VB	advcl
Child:	to	to	TO	aux
Child:	crocodiles	crocodile	NNS	dobj

Delete:	the	the	DT	

Head:	crocodiles	crocodile	NNS	
Target:	wild	wild	JJ	amod

Delete:	the	the	DT	

type: Delete
sent: The best way to economize [-money-] is by cutting down unnecessary expenses .

Head:	way	way	NN	
Target:	economize	economize	VB	relcl
Child:	to	to	TO	aux

Delete:	money	money	NN	

Head:	is	be	VBZ	
Ta

sent: Salary range : $ 35 , 000 to $ 40,000 [-dollars-] .

Head:	range	range	NN	
Target:	40,000	40,000	CD	appos
Child:	000	000	CD	quantmod
Child:	to	to	TO	quantmod
Child:	$	$	$	quantmod

Delete:	dollars	dollar	NNS	

Head:	range	range	NN	
Target:	.	.	.	punct

Delete:	dollars	dollar	NNS	

type: Delete
sent: After this , I would like the first team to play our volleyball game , the second team , tennis and the last one to play [-the-] soccer .

Head:	one	one	NN	
Target:	play	play	VB	relcl
Child:	to	to	TO	aux
Child:	soccer	soccer	NN	dobj

Delete:	the	the	DT	

Head:	play	play	VB	
Target:	soccer	soccer	NN	dobj

Delete:	the	the	DT	

type: Delete
sent: Dear Michel , I am so sorry , but I could n't [-to-] come to your wedding because I 'm in a terrible sick , and I have a fever , a headache and a runny nose .

Head:	come	come	VB	
Target:	n't	not	RB	neg

Delete:	to	to	TO	

Head:	am	be	VBP	
Target:	come	come	VB	conj
Child:	I	-PRON-	PRP	nsubj
Child:	could	can	MD	aux
Child:	n't	not	RB	neg
Child:	to

Child:	I	-PRON-	PRP	nsubj
Child:	can	can	MD	aux
Child:	to	to	IN	prep
Child:	.	.	.	punct

Delete:	there	there	RB	

Head:	listen	listen	VB	
Target:	to	to	IN	prep
Child:	group	group	NN	pobj

Delete:	there	there	RB	

type: Delete
sent: You must be able to handle [-with-] young people and their parents well and listen and explain to them with patience .

Head:	able	able	JJ	
Target:	handle	handle	VB	xcomp
Child:	to	to	TO	aux
Child:	people	people	NNS	dobj
Child:	well	good	RB	advmod
Child:	and	and	CC	cc
Child:	listen	listen	VB	conj

Delete:	with	with	IN	

Head:	people	people	NNS	
Target:	young	young	JJ	amod

Delete:	with	with	IN	

type: Delete
sent: You are more confident to face [-the-] real life .

Head:	confident	confident	JJ	
Target:	face	face	VB	xcomp
Child:	to	to	TO	aux
Child:	life	life	NN	dobj

Delete:	the	the	DT	

Head:	life	life	NN	
Target:	real	real	JJ	amod

Delete:	the	the	DT	

type: Delete
sent: TOEIC is useful in companies for recruiting or communicating .It could be used by stude

...

Child:	healthy	healthy	JJ	acomp

Delete:	more	much	JJR	

Head:	be	be	VB	
Target:	healthy	healthy	JJ	acomp

Delete:	more	much	JJR	

type: Delete
sent: Sally wishes to meet [-with-] me soon .

Head:	wishes	wish	VBZ	
Target:	meet	meet	VB	xcomp
Child:	to	to	TO	aux
Child:	me	-PRON-	PRP	dobj
Child:	soon	soon	RB	advmod

Delete:	with	with	IN	

Head:	meet	meet	VB	
Target:	me	-PRON-	PRP	dobj

Delete:	with	with	IN	

type: Delete
sent: They 're so much worried about this , because our company is very far and there are no public transports easily available to go [-to-] where the company is located .

Head:	available	available	JJ	
Target:	go	go	VB	xcomp
Child:	to	to	TO	aux
Child:	located	locate	VBN	advcl

Delete:	to	to	TO	

Head:	located	locate	VBN	
Target:	where	where	WRB	advmod

Delete:	to	to	TO	

type: Delete
sent: I do n't know and I only guess that I have to do [-every-] my every work very well .

Head:	have	have	VBP	
Target:	do	do	VB	xcomp
Child:	to	to	TO	aux
Child:	work	work	NN	dobj
Child:	we

sent: Please [-everyone-] come to my home early .

Head:	come	come	VB	
Target:	Please	please	UH	intj

Delete:	everyone	everyone	NN	

Head:	come	come	VB	
Target:	come	come	VB	ROOT
Child:	Please	please	UH	intj
Child:	to	to	IN	prep
Child:	early	early	RB	advmod
Child:	.	.	.	punct

Delete:	everyone	everyone	NN	

type: Delete
sent: You like to go [-to-] shopping .

Head:	like	like	VBP	
Target:	go	go	VB	xcomp
Child:	to	to	TO	aux
Child:	shopping	shop	NN	xcomp

Delete:	to	to	TO	

Head:	go	go	VB	
Target:	shopping	shop	NN	xcomp

Delete:	to	to	TO	

type: Delete
sent: Next , I will work as an intern after graduation . This can help me get more opportunities to get [-my-] experience and increase my employment prospects 3 .

Head:	opportunities	opportunity	NNS	
Target:	get	get	VB	acl
Child:	to	to	TO	aux
Child:	experience	experience	NN	dobj
Child:	and	and	CC	cc
Child:	increase	increase	VB	conj

Delete:	my	-PRON-	PRP$	

Head:	get	get	VB	
Target:	experience	experience	NN	dobj

Delete:	my	-PRON-	PRP$	

t


Head:	finish	finish	VB	
Target:	college	college	NN	dobj

Delete:	the	the	DT	

type: Delete
sent: After to listened [-for-] several times , I was sing it again .

Head:	After	after	IN	
Target:	listened	listen	VBD	pcomp
Child:	to	to	TO	aux
Child:	times	time	NNS	npadvmod

Delete:	for	for	IN	

Head:	times	time	NNS	
Target:	several	several	JJ	amod

Delete:	for	for	IN	

type: Delete
sent: The guy [-still-] went to school on the next day , and after that , he killed himself .

Head:	went	go	VBD	
Target:	guy	guy	NN	nsubj
Child:	The	the	DT	det

Delete:	still	still	RB	

Head:	went	go	VBD	
Target:	went	go	VBD	ROOT
Child:	guy	guy	NN	nsubj
Child:	to	to	IN	prep
Child:	on	on	IN	prep
Child:	,	,	,	punct
Child:	and	and	CC	cc
Child:	killed	kill	VBD	conj

Delete:	still	still	RB	

type: Delete
sent: On the weekend , l go once or twice to [-the-] swim .

Head:	swim	swim	VB	
Target:	to	to	TO	aux

Delete:	the	the	DT	

Head:	go	go	VB	
Target:	swim	swim	VB	advcl
Child:	to	to	TO	aux

Delete:	the	the	DT	

type: 

Child:	to	to	TO	aux
Child:	planes	plane	NNS	dobj

Delete:	to	to	TO	

Head:	planes	plane	NNS	
Target:	all	all	PDT	predet

Delete:	to	to	TO	

type: Delete
sent: Aalen is [-in　the-] near to Stuttgart .

Head:	is	be	VBZ	
Target:	is	be	VBZ	ROOT
Child:	Aalen	aalen	NNP	nsubj
Child:	near	near	JJ	acomp
Child:	.	.	.	punct

Delete:	in	in	IN	
Delete:	the	the	DT	

Head:	is	be	VBZ	
Target:	near	near	JJ	acomp
Child:	to	to	IN	prep

Delete:	in	in	IN	
Delete:	the	the	DT	

type: Delete
sent: When my boss has a problem , he talks [-it-] to us .

Head:	talks	talk	VBZ	
Target:	talks	talk	VBZ	ROOT
Child:	has	have	VBZ	advcl
Child:	,	,	,	punct
Child:	he	-PRON-	PRP	nsubj
Child:	to	to	IN	prep
Child:	.	.	.	punct

Delete:	it	-PRON-	PRP	

Head:	talks	talk	VBZ	
Target:	to	to	IN	prep
Child:	us	-PRON-	PRP	pobj

Delete:	it	-PRON-	PRP	

type: Delete
sent: In the summer people like playing basketball , volleyball and like to go [-on-] swimming .

Head:	like	like	VBP	
Target:	go	go	VB	xcomp
Child:	to	to	TO	aux
Child:	swim

Child:	with	with	IN	prep

Delete:	a	a	DT	

type: Delete
sent: Looking at the positive side of things is important for growth , is something spiritual or something rewarding because you can develop and persue happiness ... who does n't want to achieve [-the-] happiness ?

Head:	want	want	VB	
Target:	achieve	achieve	VB	xcomp
Child:	to	to	TO	aux
Child:	happiness	happiness	NN	dobj

Delete:	the	the	DT	

Head:	achieve	achieve	VB	
Target:	happiness	happiness	NN	dobj

Delete:	the	the	DT	

type: Delete
sent: Also , is most likely that an artist to eat [-a-] peanut butter that a sports celebrity .

Head:	artist	artist	NN	
Target:	eat	eat	VB	acl
Child:	to	to	TO	aux
Child:	butter	butter	NN	dobj

Delete:	a	a	DT	

Head:	butter	butter	NN	
Target:	peanut	peanut	NN	compound

Delete:	a	a	DT	

type: Delete
sent: The smartphone allows me to quickly text [-with-] another person .

Head:	allows	allow	VBZ	
Target:	text	text	VB	ccomp
Child:	me	-PRON-	PRP	nsubj
Child:	to	to	TO	aux
Child:	quickly	quickly	RB	adv